# Import and plot downloaded CMIP6 data 

- make sure everything looks correct and reasonable

### Necessary Packages


In [1]:
import xarray as xr
import pandas as pd
import numpy as np
import cftime

from tqdm.notebook import tqdm
import re
import os

import glob

import matplotlib.pyplot as plt


In [3]:
# Get config file ~ now to use as reference for where files are stored
import download_config as cfg
from climate_utils import global_mean
from climate_utils import fix_lons

In [4]:
## I just want to keep my units please
xr.set_options(keep_attrs=True)  

### Open files

- gets model names from directories
- gets member_id from file name
- stitches together historical and SSP885 for each member_id (n.b processed data should be from 1980-2014 for historical and 2015-2100 for SSP)
  

### get list of models from directory names 

In [5]:
data_dir = cfg.lpaths['raw_data_dir']

In [6]:
models = [path.split('/')[-1] for path in glob.glob(f'{data_dir}/*')]
models.sort()  ### put them in alphabetical order 
models

['BCC-CSM2-MR',
 'CAMS-CSM1-0',
 'CESM2-WACCM',
 'CNRM-CM6-1',
 'CNRM-ESM2-1',
 'CanESM5',
 'CanESM5-CanOE',
 'FIO-ESM-2-0',
 'GFDL-CM4',
 'IPSL-CM6A-LR',
 'MPI-ESM1-2-HR',
 'MPI-ESM1-2-LR',
 'UKESM1-0-LL']

In [10]:
## place to store all the models
dict_ds = {}

## replace with for loop through available models 
for model in tqdm(models):
    print(f'Processing {model}')

    ## define model directory to subset
    model_dir = f'{data_dir}/{model}'
    ## collect unique member_ids in model directory
    member_ids = np.unique([path.split('_')[-3] for path in glob.glob(f'{model_dir}/*.nc')])
    
    tmp = {}
    ## replace with for loop through unique member_ids
    for member_id in member_ids:
        ## for each member_ids, stitch historical and SSP forcing:
        tmp[member_id] = xr.open_mfdataset(glob.glob(f'{model_dir}/*_{member_id}_*.nc'))

    ## create a temporary list
    data_arrays = []
    for member_id, da in tmp.items():
        ## assign the member_id as a coordinate
        data_arrays.append(da.assign_coords(member_id=member_id))
    
    ## concat along 'member_id' dim
    dict_ds[model] = xr.concat(data_arrays, dim='member_id')

  0%|          | 0/13 [00:00<?, ?it/s]

Processing BCC-CSM2-MR
Processing CAMS-CSM1-0
Processing CESM2-WACCM
Processing CNRM-CM6-1
Processing CNRM-ESM2-1
Processing CanESM5
Processing CanESM5-CanOE
Processing FIO-ESM-2-0
Processing GFDL-CM4
Processing IPSL-CM6A-LR
Processing MPI-ESM1-2-HR
Processing MPI-ESM1-2-LR
Processing UKESM1-0-LL


## Adjust land fraction

CanESM5, CanESM5-CanOE, and GFDL-CM4 are plotting 0 values in the ocean. Convert them to NaNs using the native land fraction. 
n.b. all land fraction .ncs are for ssp585, r1i1p1f1 (where available)

In [28]:
fix_fraction_models = ['CanESM5', 'CanESM5-CanOE', 'GFDL-CM4']

for model in tqdm(fix_fraction_models):
    print(f'Masking {model} with original land fraction')
    
    fn = glob.glob(f'{data_dir}/sftlf_fx_{model}*.nc')
    ds = fix_lons(xr.open_dataset(fn[0]).load())
    ## fix lons so that they go from -180 to 180
    land_mask = (ds.sftlf > 0)
    
    dict_ds[model]['mrsos'] = dict_ds[model]['mrsos'].where(land_mask.broadcast_like(dict_ds[model]['mrsos']), drop = True)

  0%|          | 0/3 [00:00<?, ?it/s]

Masking CanESM5 with original land fraction
Masking CanESM5-CanOE with original land fraction
Masking GFDL-CM4 with original land fraction


## Plot all the models to check things look correct

This takes 15-30 seconds

In [29]:
fig, ax = plt.subplots(ncols = 3, nrows = len(models), figsize = (15, 40), dpi = 300)

month_labels = ['Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']
## for climatology plots

for i, model in enumerate(dict_ds.keys()):
    ds = dict_ds[model]

    ## loop through member_ids to check those look normal 
    for member_id in ds.member_id:
        global_mean(ds.sel(member_id = member_id)).mrsos.plot(ax = ax[i, 1], alpha = 0.2)
        global_mean(ds.sel(member_id = member_id)).groupby('time.month').mean().mrsos.plot(ax = ax[i, 2], alpha = 0.2)

    ## plot average across all member_ids
    ds.mrsos.mean(dim = 'member_id').mean(dim = 'time').plot(ax = ax[i, 0], cmap = 'BrBG')#, levels = 10)
    global_mean(ds).mean(dim = 'member_id').mrsos.plot(ax = ax[i, 1], color = 'k')
    global_mean(ds).groupby('time.month').mean().mean(dim = 'member_id').mrsos.plot(ax = ax[i, 2], color = 'k')

    ax[i,0].set_ylabel(model, fontsize = 15, fontweight = 'bold')
    ax[i,2].set_xticks(range(1, 13))  # Set 12 ticks at positions 1 to 12
    ax[i,2].set_xticklabels(month_labels)  ## add fancy month labels

    ax[i,0].set_title(f'ensemble member count: {len(ds.member_id.data)}')
    ax[i,1].set_title(None)
    ax[i,2].set_title(None)


plt.tight_layout()


In [30]:
## looks like several models are setting soil moisture to 0 rather than NaN for ocean values

## two solutions, turn all the zeros into NaNs ourselves (I think the only model this may be a problem for is MPI-ESM1-2-HR)
## get the land-fraction for each model and only look at those areas
for model in dict_ds.keys():
    ds = dict_ds[model].load()
    print(f'{model}: {ds.mrsos.min().data}')

BCC-CSM2-MR: 0.0012752028414979577
CAMS-CSM1-0: 5.012521266937256
CESM2-WACCM: 5.114418983459473
CNRM-CM6-1: 5.391859531402588
CNRM-ESM2-1: 5.740179061889648
CanESM5: 4.0828938484191895
CanESM5-CanOE: 4.0868916511535645
FIO-ESM-2-0: 2.8038105964660645
GFDL-CM4: 0.0
IPSL-CM6A-LR: 5.972583293914795
MPI-ESM1-2-HR: 0.0
MPI-ESM1-2-LR: 3.5989489555358887
UKESM1-0-LL: 0.12615966796875


## calculate zscore

### GWL 

TO DO:
- get GWL for each model 